In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
import tensorflow as tf
import random
from math import pi

In [5]:
squares = [chr(i) for i in range(0x1F7E5, 0x1F7EC)]
tfsquares = tf.constant(squares)
print(squares)
colors = tf.constant([10, 219, 38, 48, 80,  282, 20] * tf.constant(pi/180.0), dtype=tf.float32)
color_vectors = tf.transpose(
    tf.stack([
    tf.math.cos(colors),
    tf.math.sin(colors)]
    )
)
color_vectors

['🟥', '🟦', '🟧', '🟨', '🟩', '🟪', '🟫']


<tf.Tensor: shape=(7, 2), dtype=float32, numpy=
array([[ 0.9848077 ,  0.17364818],
       [-0.777146  , -0.62932044],
       [ 0.7880108 ,  0.6156615 ],
       [ 0.6691306 ,  0.74314487],
       [ 0.17364822,  0.9848077 ],
       [ 0.20791148, -0.9781476 ],
       [ 0.9396926 ,  0.34202012]], dtype=float32)>

In [11]:
def one_hot_to_string(tensor):
    square_select = tf.math.argmax(tensor, 2)

    tfstring = tf.strings.join(
        tf.map_fn(
            lambda v:
            tf.strings.join(
                tf.gather(tfsquares, tf.cast(v, tf.int64))), square_select, fn_output_signature=tf.string), "\n")

    return tfstring.numpy().decode()

def index_to_string(tensor):
    return tf.argmax((tf.einsum("ijk,lk->ijl", tensor, color_vectors)), axis=2)


In [57]:
vi = tf.map_fn(lambda v: tf.map_fn(lambda s: color_vectors[s],v, fn_output_signature=tf.float32),tf.constant(e, shape=(8, 8)),fn_output_signature=tf.float32)

index_to_string(vi)

<tf.Tensor: shape=(8, 8), dtype=int64, numpy=
array([[5, 0, 1, 3, 3, 2, 4, 0],
       [3, 2, 3, 6, 5, 3, 0, 5],
       [1, 3, 0, 1, 6, 4, 5, 3],
       [3, 5, 0, 6, 5, 5, 0, 3],
       [0, 3, 0, 6, 6, 1, 5, 2],
       [4, 1, 4, 6, 6, 1, 0, 5],
       [6, 0, 2, 5, 0, 1, 5, 4],
       [0, 2, 5, 4, 1, 5, 0, 4]])>

In [10]:
# def colors_to_one_hot(tensor):
vi = tf.map_fn(lambda v: tf.map_fn(lambda s: color_vectors[s],v, fn_output_signature=tf.float32),tf.constant(e, shape=(8, 8)),fn_output_signature=tf.float32)
ns = tf.image.extract_patches(tf.constant(vi, shape=(1,8,8,2)), (1,3,3,1), (1,1,1,1), (1,1,1,1), padding="SAME")
virs = tf.reshape(vi, (8*8,2))
# tf.reduce_sum(tf.multiply(tf.repeat(vi, 9, -1), ns))
tf.abs(tf.einsum("...k,...k->...", tf.repeat(vi, 9, -1), ns))

<tf.Tensor: shape=(1, 8, 8), dtype=float32, numpy=
array([[[0.71719116, 0.04602498, 1.0273366 , 2.9402392 , 2.4437628 ,
         1.0988994 , 1.7921778 , 0.6444071 ],
        [1.2672982 , 1.8689629 , 3.8761568 , 2.4126112 , 2.840665  ,
         3.0419385 , 4.8909955 , 3.583321  ],
        [0.4506898 , 0.01335579, 3.258954  , 3.80125   , 6.4259176 ,
         6.3595123 , 6.609476  , 1.6973627 ],
        [1.8337119 , 1.4464988 , 4.6484404 , 4.2732587 , 7.6358337 ,
         5.4232316 , 4.313001  , 1.6071305 ],
        [4.9838686 , 1.3140092 , 1.5253077 , 1.9003649 , 6.782009  ,
         3.5835938 , 4.203249  , 1.5495552 ],
        [5.3104043 , 5.0123706 , 3.3745103 , 4.540594  , 6.6606255 ,
         3.9076035 , 4.9301    , 3.4342353 ],
        [3.3523657 , 4.9394774 , 5.672796  , 4.8756404 , 7.1605525 ,
         8.192585  , 7.06907   , 4.199152  ],
        [0.13434029, 4.039145  , 6.2488484 , 3.2168784 , 5.319997  ,
         5.4898353 , 5.301211  , 1.6475667 ]]], dtype=float32)>

In [27]:
oh = tf.one_hot(3, 7)
print(oh)
print(tf.where(oh))

# a = tf.constant([[list(tf.one_hot(random.randrange(7), 7)) for i in range(8) ] for i in range(8)], shape=(8,8,len(squares)))

# print([[list(tf.one_hot(random.randrange(7), 7)) for i in range(8) ] for i in range(8)])
e = [[random.randrange(7) for i in range(8)] for i in range(8)]
# print(e)

a = tf.one_hot(tf.constant(e, shape=(8, 8)), len(squares))

print(one_hot_to_string(a))
# print("--------------")
# print(one_hot_to_string(tf.reverse(a, axis=(-2,))))
# print("--------------")
# print(one_hot_to_string(tf.reverse(a, axis=(-3,))))
# print("--------------")
# print(one_hot_to_string(tf.transpose(a, perm=(1,0,2))))
print("--------------")
# print(one_hot_to_string(tf.reverse(tf.transpose(tf.reverse(a, axis=(-2,)), perm=(1,0,2)), axis=(-2,))))
print(one_hot_to_string(tf.reverse(a, axis=(-2,-3,))))
# print(tensor_to_string(tf.transpose(a, [1, 0, 2])))
# print("--------------")
# print(tensor_to_string(tf.linalg.matmul( a , tf.constant(
#     [
#         [0, 0, 0, 0, 0, 0, 0, 1],
#         [0, 0, 0, 0, 0, 0, 1, 0],
#         [0, 0, 0, 0, 0, 1, 0, 0],
#         [0, 0, 0, 0, 1, 0, 0, 0],
#         [0, 0, 0, 1, 0, 0, 0, 0],
#         [0, 0, 1, 0, 0, 0, 0, 0],
#         [0, 1, 0, 0, 0, 0, 0, 0],
#         [1, 0, 0, 0, 0, 0, 0, 0]
#     ], dtype=tf.float32, shape=(8,8,1)
# ), transpose_a=True)))
# print("--------------")
# print(tensor_to_string(tf.reverse(a, (0,))))
# print("--------------")
# print(tensor_to_string(tf.reverse(a, (1,))))
# print(tensor_to_string(
#     tf.linalg.matmul(
#         tf.transpose(a, [0, 2, 1]),
#         tf.reverse(a, (1,)))
# ))
print(
    tf.einsum(
        "ijk,ijk->ij",
        a,
        tf.reverse(a, (1,)))
)


# print(tf.constant(range(6), shape=(2,3)))
# tf.map_fn(tf.math.reduce_sum, tf.constant(range(6), shape=(2,3)))


tf.Tensor([0. 0. 0. 1. 0. 0. 0.], shape=(7,), dtype=float32)
tf.Tensor([[3]], shape=(1, 1), dtype=int64)
🟨🟥🟨🟨🟩🟫🟪🟫
🟩🟪🟧🟧🟦🟧🟦🟫
🟩🟦🟫🟨🟦🟨🟩🟫
🟪🟫🟩🟨🟧🟪🟥🟩
🟥🟫🟨🟫🟧🟦🟦🟧
🟩🟫🟫🟧🟨🟨🟪🟫
🟩🟪🟦🟥🟧🟫🟧🟨
🟨🟪🟨🟧🟪🟦🟨🟧
--------------
🟧🟨🟦🟪🟧🟨🟪🟨
🟨🟧🟫🟧🟥🟦🟪🟩
🟫🟪🟨🟨🟧🟫🟫🟩
🟧🟦🟦🟧🟫🟨🟫🟥
🟩🟥🟪🟧🟨🟩🟫🟪
🟫🟩🟨🟦🟨🟫🟦🟩
🟫🟦🟧🟦🟧🟧🟪🟩
🟫🟪🟫🟩🟨🟨🟥🟨
tf.Tensor(
[[0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 1. 0. 0. 1. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0. 0.]], shape=(8, 8), dtype=float32)


In [15]:
import aesthetic_loss

es = [[[random.randrange(7) for i in range(8)]
      for i in range(8)] for j in range(16)]

vis = tf.stack(
    [tf.map_fn(lambda v: tf.map_fn(lambda s: color_vectors[s], v, fn_output_signature=tf.float32), tf.constant(
        e, shape=(8, 8)), fn_output_signature=tf.float32) for e in es]
)

aesthetic_loss.aesthetic_loss(vis)
# aesthetic_loss.compute_score(vis, vis)
# tf.linalg.l2_normalize(vis, axis=-1)

<tf.Tensor: shape=(), dtype=float32, numpy=-0.08645747>

In [91]:
x = tf.Variable(2)
y = tf.Variable(3)

xp = tf.pow(x, [0,1,2,3])
yp = tf.pow(y, [0,1,2,3])

A = tf.Variable([[i+j for i in range(4)] for j in range(4)], shape=(4,4))
tf.einsum("i,ij,j", xp, A, yp)


<tf.Tensor: shape=(), dtype=int32, numpy=2890>

In [70]:
r = tf.random.normal((16,2))
rp = tf.map_fn(lambda v: tf.pow(tf.repeat(tf.reshape(v, shape=(2,1)), repeats=4, axis=1), tf.constant([[0,1,2,3], [0,1,2,3]], dtype=tf.float32)), r)
A = tf.Variable(tf.reshape([float(i) for i in range(8*4*4)], shape=(8,4,4)), shape=(8,4,4), dtype=tf.float32)
tf.einsum("ik,ij,lkj->il", rp[:,0], rp[:,1], A)
# rp[:,0]


<tf.Tensor: shape=(16, 8), dtype=float32, numpy=
array([[-6.07829041e+02, -1.43090210e+03, -2.25397559e+03,
        -3.07704883e+03, -3.90012207e+03, -4.72319531e+03,
        -5.54626855e+03, -6.36934229e+03],
       [-4.28289948e+01, -8.77924423e+01, -1.32755875e+02,
        -1.77719330e+02, -2.22682800e+02, -2.67646210e+02,
        -3.12609680e+02, -3.57573120e+02],
       [ 9.78072433e+01,  2.85662659e+02,  4.73518066e+02,
         6.61373413e+02,  8.49228882e+02,  1.03708435e+03,
         1.22493982e+03,  1.41279517e+03],
       [ 3.64326048e+00,  2.58858261e+01,  4.81283913e+01,
         7.03709641e+01,  9.26135254e+01,  1.14856094e+02,
         1.37098648e+02,  1.59341217e+02],
       [-1.08920467e+00,  3.87969995e+00,  8.84860516e+00,
         1.38175116e+01,  1.87864113e+01,  2.37553177e+01,
         2.87242279e+01,  3.36931267e+01],
       [ 2.75129032e+01,  9.32729721e+01,  1.59033051e+02,
         2.24793137e+02,  2.90553192e+02,  3.56313324e+02,
         4.22073334e+02,  4.

In [82]:
import polymap
r = tf.random.normal((16,2))

pm = polymap.Polymap(8,4)
# pm.build([16,2])
print(pm(r))


tf.Tensor(
[[ 4.15302128e-01 -1.17927468e+00  2.49658436e-01  6.19551420e-01
  -1.39033377e-01  2.79209971e-01  3.97601783e-01 -2.17277408e-01]
 [ 1.74276757e+00  5.69359064e-02  5.38259745e-04  1.49045396e+00
  -7.87080288e-01 -3.98119450e-01  1.18716180e-01  1.86502957e+00]
 [ 1.78081155e+00 -1.29199183e+00 -5.72377980e-01  1.73489356e+00
  -1.81523621e+00 -7.56731749e-01  5.50791979e-01  2.23066378e+00]
 [-2.86107287e-02  2.38285348e-01 -2.90394664e-01  2.20198780e-02
   3.43291536e-02  2.77290910e-01 -3.25144343e-02  3.50418538e-01]
 [-2.32135087e-01  1.95894271e-01  5.75335659e-02 -1.76543556e-03
  -4.01449911e-02  2.00845733e-01 -9.64274257e-02  2.31855541e-01]
 [ 4.60646629e-01  7.75275290e-01 -9.96064782e-01 -5.15016496e-01
   2.03099363e-02  7.87942708e-02 -3.07008505e-01  7.16598153e-01]
 [ 3.02803397e-01 -8.83126408e-02  3.72119397e-01  1.14753373e-01
  -8.30153376e-03  6.69163764e-02 -3.60930443e-01  4.32033747e-01]
 [-1.55036688e-01  2.96032988e-02  5.69820963e-02 -1.04342

In [111]:
r = tf.random.normal(shape = (16, 8, 8, 2))
tf.linalg.l2_normalize(r,axis=-1)

<tf.Tensor: shape=(16, 8, 8, 2), dtype=float32, numpy=
array([[[[ 0.26760346,  0.9635291 ],
         [ 0.92846906,  0.37140968],
         [ 0.43006882,  0.90279603],
         ...,
         [ 0.9174245 ,  0.39790976],
         [ 0.68369484,  0.729768  ],
         [ 0.5905379 , -0.8070098 ]],

        [[-0.9665002 ,  0.25666556],
         [ 0.6174854 , -0.7865824 ],
         [-0.8356619 , -0.54924417],
         ...,
         [-0.42570287,  0.90486294],
         [ 0.99368197,  0.11223278],
         [ 0.22659355,  0.97398937]],

        [[ 0.9998629 ,  0.01655844],
         [-0.02171519,  0.9997642 ],
         [ 0.765471  , -0.64347047],
         ...,
         [-0.45096368,  0.8925422 ],
         [ 0.23687297,  0.9715406 ],
         [-0.2564354 ,  0.9665613 ]],

        ...,

        [[ 0.99743736, -0.07154454],
         [-0.421027  ,  0.907048  ],
         [-0.06904475,  0.99761355],
         ...,
         [-0.14730097, -0.9890917 ],
         [-0.76936895, -0.63880455],
         [ 0.12321